In [1]:
from cassandra_client import CassandraClient
import uuid
from datetime import datetime
import random
import threading
import time
from datetime import datetime, timedelta
from collections import defaultdict

In [2]:
client = CassandraClient()
no_of_repetitions = 10000
no_of_books = 1000
no_of_users = 3

In [6]:
def stress_test_1(client, repetitions=no_of_repetitions):
    """The client makes the same request very quickly min (10000 times)."""

    client.delete_all_reservations()
    print("Deleted all reservations")

    user_id = uuid.uuid4()
    book_id = uuid.UUID('1da069d2-b97b-4503-8aac-0c685ac75845')
    reservation_ids = []
    for i in range(repetitions):
        reservation_id = client.make_reservation(user_id, book_id)
        if reservation_id:
            reservation_ids.append(reservation_id)
            print(f"Iteration {i+1}: Created reservation with ID {reservation_id}")
        else:
            print(f"Iteration {i+1}: Failed to create reservation, book already reserved or does not exist.")
        if i % 100 == 0:
            print(f"Iteration {i+1}")
    print(f"Created {len(reservation_ids)} reservations in total")
    
stress_test_1(client)

Deleted all reservations
Created 1 reservations in total


In [7]:
def stress_test_2(client, no_of_users, no_of_books, repetitions=no_of_repetitions):
    """Two or more clients make the possible requests randomly."""

    client.delete_all_reservations()
    print("Deleted all reservations")

    successful_reservations = 0
    unsuccessful_reservations = 0

    # Generate user IDs dynamically based on the number of users
    user_ids = [uuid.uuid4() for _ in range(no_of_users)]
    user_reservation_counts = defaultdict(int)

    # Insert new books
    book_ids = [uuid.uuid4() for _ in range(no_of_books)]
    for i, book_id in enumerate(book_ids):
        client.insert_book(book_id, f"Book {i+1}", f"Author {i+1}", "2024-01-01")
    print(f"Inserted {no_of_books} new books for the test")

    def make_random_request(user_id):
        nonlocal successful_reservations, unsuccessful_reservations
        for _ in range(repetitions):
            book_id = random.choice(book_ids)
            reservation_id = client.make_reservation(user_id, book_id)
            if reservation_id:
                successful_reservations += 1
                user_reservation_counts[user_id] += 1
                print(f"User {str(user_id)[:8]} created reservation for book {str(book_id)[:8]} with reservation ID {str(reservation_id)[:8]}")
            else:
                unsuccessful_reservations += 1
                print(f"User {str(user_id)[:8]} failed to create reservation for book {str(book_id)[:8]} - Book might be already reserved or does not exist")

    threads = []
    for user_id in user_ids:
        t = threading.Thread(target=make_random_request, args=(user_id,))
        t.start()
        threads.append(t)
        print(f"Started thread for user {str(user_id)[:8]}")

    for t in threads:
        t.join()

    print(f"Completed {no_of_users * repetitions} random reservations")
    print(f"Successful reservations: {successful_reservations}")
    print(f"Unsuccessful reservations: {unsuccessful_reservations}")

    # Check how many books are reserved by each user and how many books haven't been reserved at all
    reservations_by_user = defaultdict(int)
    books_not_reserved = set(book_ids)

    for book_id in book_ids:
        reservation = client.get_reservation_by_book_id(book_id)
        if reservation:
            reservations_by_user[reservation.user_id] += 1
            books_not_reserved.discard(book_id)

    for user_id in user_ids:
        print(f"Books reserved by user {str(user_id)[:8]}: {reservations_by_user[user_id]}")

    print(f"Books not reserved by any user: {len(books_not_reserved)}")

    # Clean up books after the test
    for book_id in book_ids:
        client.delete_book(book_id)
    print(f"Deleted {no_of_books} books after the test")


stress_test_2(client, no_of_users, no_of_books)


Deleted all reservations
Inserted 1000 new books for the test
Started thread for user 1912ba0c
Started thread for user 5e0d3143
Started thread for user 2ba4258c
User 1912ba0c created reservation for book e4d64332 with reservation ID 5c3e539f
User 5e0d3143 created reservation for book f89df7bb with reservation ID af2baff2
User 2ba4258c created reservation for book 0fd5bb68 with reservation ID 84d52ed0
User 1912ba0c created reservation for book 4a7edec5 with reservation ID fc6f3f7e
User 5e0d3143 created reservation for book 5aa74423 with reservation ID 9ab69278
User 2ba4258c created reservation for book 1512cb1f with reservation ID 419378e4
User 1912ba0c created reservation for book aa051172 with reservation ID 566fe037
User 5e0d3143 created reservation for book d85e6a3a with reservation ID 0b7ef1a8
User 2ba4258c created reservation for book 28ba82f8 with reservation ID b117ecd5
User 1912ba0c created reservation for book 0fd7c63b with reservation ID 9d136206
User 5e0d3143 created reserva

In [3]:
def stress_test_3(client, no_of_books):
    """Immediate occupancy of all seats/reservations by 2 clients."""

    client.delete_all_reservations()
    print("Deleted all reservations")

    # Insert new books for the test
    book_ids = [uuid.uuid4() for _ in range(no_of_books)]
    for i, book_id in enumerate(book_ids):
        client.insert_book(book_id, f"Book {i+1}", f"Author {i+1}", "2024-01-01")
    print(f"Inserted {no_of_books} new books for the test")

    # Generate user IDs
    user_id_1 = uuid.uuid4()
    user_id_2 = uuid.uuid4()
    successful_reservations_user1 = 0
    unsuccessful_reservations_user1 = 0
    successful_reservations_user2 = 0
    unsuccessful_reservations_user2 = 0

    def make_reservations(user_id, successful_reservations, unsuccessful_reservations, books):
        for book_id in books:
            reservation_id = client.make_reservation(user_id, book_id)
            if reservation_id:
                successful_reservations += 1
                print(f"User {user_id} made reservation with ID {reservation_id} for book {book_id}")
            else:
                unsuccessful_reservations += 1
                print(f"User {user_id} failed to make reservation for book {book_id}")
        return successful_reservations, unsuccessful_reservations

    def user1_reservations():
        nonlocal successful_reservations_user1, unsuccessful_reservations_user1
        books_user1 = book_ids
        successful_reservations_user1, unsuccessful_reservations_user1 = make_reservations(user_id_1, successful_reservations_user1, unsuccessful_reservations_user1, books_user1)

    def user2_reservations():
        nonlocal successful_reservations_user2, unsuccessful_reservations_user2
        books_user2 = book_ids[::-1]
        successful_reservations_user2, unsuccessful_reservations_user2 = make_reservations(user_id_2, successful_reservations_user2, unsuccessful_reservations_user2, books_user2)

    t1 = threading.Thread(target=user1_reservations)
    t2 = threading.Thread(target=user2_reservations)

    t1.start()
    t2.start()
    print("Both threads started")

    t1.join()
    t2.join()
    print("Both threads completed")

    print(f"User {user_id_1} successful reservations: {successful_reservations_user1}")
    print(f"User {user_id_1} unsuccessful reservations: {unsuccessful_reservations_user1}")
    print(f"User {user_id_2} successful reservations: {successful_reservations_user2}")
    print(f"User {user_id_2} unsuccessful reservations: {unsuccessful_reservations_user2}")

    # Check how many books are reserved by each user
    reservations_user1 = 0
    reservations_user2 = 0
    reservations_none = 0

    for book_id in book_ids:
        reservation = client.get_reservation_by_book_id(book_id)
        if reservation:
            if reservation.user_id == user_id_1:
                reservations_user1 += 1
            elif reservation.user_id == user_id_2:
                reservations_user2 += 1
        else:
            reservations_none += 1

    print(f"Books reserved by user {user_id_1}: {reservations_user1}")
    print(f"Books reserved by user {user_id_2}: {reservations_user2}")
    print(f"Books reserved by none: {reservations_none}")

    # Clean up books after the test
    for book_id in book_ids:
        client.delete_book(book_id)
    print(f"Deleted {no_of_books} books after the test")

stress_test_3(client, no_of_books)

Deleted all reservations
Inserted 1000 new books for the test
Both threads started
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:12.695912
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:12.735098
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:12.782767
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:12.828999
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:12.870976
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:12.946166
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:12.982576
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:13.020584
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:13.060038
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:13.102094
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:13.127937
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:13.159587
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:13.203876
099d1e5f-a1fa-4e33-9454-4865e87e89ec : 2024-06-03 10:25:13.

In [ ]:
def stress_test_4(client, repetitions=no_of_repetitions):
    """Constant cancellations and seat occupancy for the same seat (10000 times)."""

    client.delete_all_reservations()
    print("Deleted all reservations")

    # Insert a single book for the test
    book_id = uuid.uuid4()
    book_id_short = str(book_id)[:8]
    client.insert_book(book_id, "Test Book", "Test Author", "2024-01-01")
    print(f"Inserted book with ID {book_id_short} for the test")

    # Generate user IDs
    user_id_1 = uuid.uuid4()
    user_id_2 = uuid.uuid4()
    user_id_1_short = str(user_id_1)[:8]
    user_id_2_short = str(user_id_2)[:8]

    def reserve_and_cancel(user_id, user_id_short):
        for i in range(repetitions):
            reservation_id = client.make_reservation(user_id, book_id)
            if reservation_id:
                reservation_id_short = str(reservation_id)[:8]
                print(f"User {user_id_short} made reservation with ID {reservation_id_short} for book {book_id_short}")
                # Introduce a random short delay to create overlap
                time.sleep(random.uniform(0.01, 0.05))
                client.cancel_reservation(reservation_id)
                print(f"User {user_id_short} cancelled reservation with ID {reservation_id_short} for book {book_id_short}")
            else:
                print(f"User {user_id_short} failed to make reservation for book {book_id_short}")

    t1 = threading.Thread(target=reserve_and_cancel, args=(user_id_1, user_id_1_short))
    t2 = threading.Thread(target=reserve_and_cancel, args=(user_id_2, user_id_2_short))

    t1.start()
    t2.start()
    print("Both threads started")

    t1.join()
    t2.join()
    print("Both threads completed")

    # Clean up book after the test
    client.delete_book(book_id)
    print(f"Deleted book with ID {book_id_short} after the test")

stress_test_4(client)

Deleted all reservations
Inserted book with ID 7ed82f7e for the test
Both threads started
User 1f37c40f made reservation with ID c5076db5 for book 7ed82f7e
User 1f37c40f cancelled reservation with ID c5076db5 for book 7ed82f7e
User f0501c0c made reservation with ID 55408ff6 for book 7ed82f7e
User 1f37c40f failed to make reservation for book 7ed82f7e
User f0501c0c cancelled reservation with ID 55408ff6 for book 7ed82f7e
User 1f37c40f made reservation with ID 61437d56 for book 7ed82f7e
User f0501c0c failed to make reservation for book 7ed82f7e
User 1f37c40f cancelled reservation with ID 61437d56 for book 7ed82f7e
User f0501c0c made reservation with ID fe006bc7 for book 7ed82f7e
User 1f37c40f failed to make reservation for book 7ed82f7e
User f0501c0c cancelled reservation with ID fe006bc7 for book 7ed82f7e
User 1f37c40f made reservation with ID 4eee85c0 for book 7ed82f7e
User f0501c0c failed to make reservation for book 7ed82f7e
User 1f37c40f cancelled reservation with ID 4eee85c0 for boo

In [ ]:
def stress_test_5(client, no_of_books=no_of_books):
    """Update the date for 1000 reservations."""

    client.delete_all_reservations()
    print("Deleted all reservations")

    # Insert new books for the test
    no_of_books = 1000
    book_ids = [uuid.uuid4() for _ in range(no_of_books)]
    for i, book_id in enumerate(book_ids):
        client.insert_book(book_id, f"Book {i+1}", f"Author {i+1}", "2024-01-01")
    print(f"Inserted {no_of_books} new books for the test")

    # Generate user ID
    user_id = uuid.uuid4()
    user_id_short = str(user_id)[:8]

    # Reserve books
    reservation_ids = []
    for book_id in book_ids:
        reservation_id = client.make_reservation(user_id, book_id)
        if reservation_id:
            reservation_ids.append(reservation_id)
            reservation_id_short = str(reservation_id)[:8]
            book_id_short = str(book_id)[:8]
            print(f"User {user_id_short} made reservation with ID {reservation_id_short} for book {book_id_short}")

    # Update reservations
    def update_reservations():
        for i, reservation_id in enumerate(reservation_ids):
            new_date = datetime.now() + timedelta(days=i)
            client.update_reservation(reservation_id, new_date)
            reservation_id_short = str(reservation_id)[:8]
            print(f"Updated reservation {reservation_id_short} with new date {new_date}")

    t = threading.Thread(target=update_reservations)
    t.start()
    print("Update thread started")

    t.join()
    print("Update thread completed")

    # Clean up books after the test
    for book_id in book_ids:
        client.delete_book(book_id)
    print(f"Deleted {no_of_books} books after the test")

# Run the stress test
stress_test_5(client)


Deleted all reservations
Inserted 1000 new books for the test
User 5c72a0c4 made reservation with ID 97b9fc6f for book 3ed24bb8
User 5c72a0c4 made reservation with ID e7639788 for book 38c59e7b
User 5c72a0c4 made reservation with ID 350cc700 for book f3cb6a3c
User 5c72a0c4 made reservation with ID be657ee2 for book 8432d37b
User 5c72a0c4 made reservation with ID ea7bde6c for book 945fdd44
User 5c72a0c4 made reservation with ID da10a0cd for book cb3fbc14
User 5c72a0c4 made reservation with ID 0741bd17 for book a51e3218
User 5c72a0c4 made reservation with ID 3e3e520a for book d45c7c9b
User 5c72a0c4 made reservation with ID 13b9ac70 for book d04a8354
User 5c72a0c4 made reservation with ID c1b1aa50 for book fab2b548
User 5c72a0c4 made reservation with ID f241e034 for book c0a305b8
User 5c72a0c4 made reservation with ID a208b81f for book 7dee1e84
User 5c72a0c4 made reservation with ID a69cd924 for book e647f18a
User 5c72a0c4 made reservation with ID 9b81784c for book c4180856
User 5c72a0c4 